# Explainability for Classifiers: GradCAM, OcclusionSensitivity et al.

<table class="tfo-notebook-buttons" align="left">
  <td>
    <a target="_blank" href="https://colab.research.google.com/github/mtwenzel/teaching/blob/master/01 Explainability using tf_explain.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png" />Run in Google Colab</a>
  </td>
  <td>
    <a target="_blank" href="https://github.com/mtwenzel/teaching/blob/master/01 Explainability using tf_explain.ipynb
"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png" />View source on GitHub</a>
  </td>
</table>
<br/><br/><br/>

This notebook shows for MNIST and for a medical example (Parkinson SPECT classification) how different visualization methods compare.

The code inherits from the 'tf_explain' original authors' example code and adapts it to the Parkinson example.

Use as a basis for own experiments.

# Preparations

Install TensorFlow 2.0.0 rc0 and TFP 0.8.0 rc0 below, if not running locally.

In [0]:
#@title Remove Tensorboard logs of previous runs
#@markdown Don't execute if you don't want to loose logs. 
%rm -rf logs/

In [6]:
#@title Install TensorFlow { display-mode: "form" }
TF_Installation = 'TF2 RC0 (GPU)' #@param ['TF2 Nightly (GPU)', 'TF2 RC0 (GPU)', 'TF2 Stable (GPU)', 'TF1 Nightly (GPU)', 'TF1 Stable (GPU)','System']
# added 2.0.0-rc0
if TF_Installation == 'TF2 Nightly (GPU)':
  !pip install -q --upgrade tf-nightly-gpu-2.0-preview
  print('Installation of `tf-nightly-gpu-2.0-preview` complete.')
elif TF_Installation == 'TF2 RC0 (GPU)':
  !pip install -q --upgrade tensorflow-gpu==2.0.0-rc0
  print('Installation of `tensorflow-gpu==2.0.0-rc0` complete. Use with tensorflow_probability=0.8.0-rc0')
elif TF_Installation == 'TF2 Stable (GPU)':
  !pip install -q --upgrade tensorflow-gpu==2.0.0-alpha0
  print('Installation of `tensorflow-gpu==2.0.0-alpha0` complete.')
elif TF_Installation == 'TF1 Nightly (GPU)':
  !pip install -q --upgrade tf-nightly-gpu
  print('Installation of `tf-nightly-gpu` complete.')
elif TF_Installation == 'TF1 Stable (GPU)':
  !pip install -q --upgrade tensorflow-gpu
  print('Installation of `tensorflow-gpu` complete.')
elif TF_Installation == 'System':
  pass
else:
  raise ValueError('Selection Error: Please select a valid '
                   'installation option.')

     |████████████████████████████████| 380.5MB 62kB/s 
     |████████████████████████████████| 4.3MB 28.9MB/s 
     |████████████████████████████████| 501kB 44.3MB/s 
Installation of `tensorflow-gpu==2.0.0-rc0` complete. Use with tensorflow_probability=0.8.0-rc0


In [7]:
#@title Install tensorflow_probability { display-mode: "form" }
TFP_Installation = "0.8.0-rc0" #@param ["0.8.0-rc0", "Nightly", "Stable", "System"]

if TFP_Installation == "Nightly":
  !pip install -q tfp-nightly
  print("Installation of `tfp-nightly` complete.")
elif TFP_Installation == "0.8.0-rc0":
  !pip install -q --upgrade tensorflow-probability==0.8.0-rc0
  print("Installation of `tensorflow-probability` complete.")
elif TFP_Installation == "Stable":
  !pip install -q --upgrade tensorflow-probability
  print("Installation of `tensorflow-probability` complete.")
elif TFP_Installation == "System":
  pass
else:
  raise ValueError("Selection Error: Please select a valid "
                   "installation option.")

     |████████████████████████████████| 2.5MB 6.6MB/s 
Installation of `tensorflow-probability` complete.


In [8]:
#@title Check GPU availability and TF version. 
import tensorflow as tf

device_name = tf.test.gpu_device_name()
if device_name != '/device:GPU:0':
    print('GPU device not found')
else:
    print('Found GPU at: {}'.format(device_name))
print(tf.__version__ )# Has to be 2.0 for this notebook to work...

Found GPU at: /device:GPU:0
1.14.0


In [9]:
#@title Install required python packages and utility packages.
#@markdown This installs tf_explain and RAdam, a performant optimizer. Also downloads and imports two helper python sources.
# https://github.com/sicara/tf-explain
try:
  import tf_explain as tfx
except:
  !pip install tf_explain
  import tf_explain as tfx

# https://github.com/CyberZHG/keras-radam
try:
  from keras_radam.training import RAdamOptimizer # for TF
except:
  !pip install keras-rectified-adam
  from keras_radam.training import RAdamOptimizer
    
from urllib.request import urlopen
try:
  import utilities
except:
  url = 'https://github.com/mtwenzel/utilities/raw/master/utilities.py'
  resp = urlopen(url)
  temp = open("utilities.py", "wb")
  temp.write(resp.read())
  temp.close()
  import utilities

try:
  import data_loaders
except:
  url = 'https://github.com/mtwenzel/utilities/raw/master/data_loaders.py'
  resp = urlopen(url)
  temp = open("data_loaders.py", "wb")
  temp.write(resp.read())
  temp.close()
  import data_loaders

     |████████████████████████████████| 28.7MB 1.7MB/s 
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
  Found existing installation: opencv-python 3.4.5.20
    Uninstalling opencv-python-3.4.5.20:
      Successfully uninstalled opencv-python-3.4.5.20
  Created wheel for keras-rectified-adam: filename=keras_rectified_adam-0.12.0-cp36-none-any.whl size=14553 sha256=8a1c70845cb429244eaafd1244fb85edcb80f804e6c9763b506d165b80bccddd
  Stored in directory: /root/.cache/pip/wheels/fa/05/05/3100b49ce05a2abb466df150e75766d27416464be95a3d5e81
Successfully built keras-rectified-adam


In [0]:
#@title Further imports and setup {display-mode:"form"}
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
import tensorflow.keras.backend as K
from tensorflow.keras.layers import Input,Conv2D,Dense,GlobalAveragePooling2D,concatenate,Flatten, MaxPooling2D, BatchNormalization, Dropout, SpatialDropout2D
from tensorflow.keras.applications import InceptionV3,DenseNet121
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.preprocessing.image import ImageDataGenerator
import seaborn as sns
sns.set()
%matplotlib inline

In [11]:
#@title Prepare the data. {display-mode:'form'}
TARGET_SIZE = (96,96) # Square images because of visualization library...
paths_dict = {'train': './data/PPMI-classification/all_2d_train',
             'val': './data/PPMI-classification/all_2d_val',
             'test': './data/PPMI-classification/all_2d_val'}

train_generator, val_generator, test_generator = data_loaders.provide_PPMI_dataset(paths_dict, target_size=TARGET_SIZE)
%rm PPMI-classification.zip

download complete, extracting...
... done
Found 1097 images belonging to 2 classes.
Found 193 images belonging to 2 classes.
Found 193 images belonging to 2 classes.


# Model Definition and Training

In [0]:
#@title This is a performant model definition. It is hard to interpret visualization of this.
input_image = Input(shape=TARGET_SIZE+(1,))

x = BatchNormalization()(input_image)
x = Conv2D(filters=64, kernel_size=(3,3), activation='relu')(x)
x = BatchNormalization()(x)
x = Conv2D(filters=64, kernel_size=(3,3), activation='relu', strides=(2,2), name='EarlyConv')(x)

x = BatchNormalization()(x)
x = Conv2D(filters=96, kernel_size=(3,3), activation='relu')(x)
x = BatchNormalization()(x)
x = Conv2D(filters=96, kernel_size=(3,3), activation='relu', strides=(2,2))(x)

x = BatchNormalization()(x)
x = Conv2D(filters=96, kernel_size=(3,3), activation='relu', name='MiddleConv')(x)
x = BatchNormalization()(x)
x = Conv2D(filters=96, kernel_size=(3,3), activation='relu', strides=(2,2))(x)

x = BatchNormalization()(x)
x = Conv2D(filters=128, kernel_size=(3,3), activation='relu')(x)
x = BatchNormalization()(x)
x = Conv2D(filters=128, kernel_size=(3,3), activation='relu', name='LastConv')(x)

x = Flatten()(x)
x = BatchNormalization()(x)
x = Dense(512, activation='relu')(x)
x = Dropout(rate=0.25)(x)

preds = Dense(2,activation='softmax')(x) #final layer with softmax activation

model = Model(inputs=input_image,outputs=preds)

In [0]:
#@title Simple model definition
input_image = Input(shape=TARGET_SIZE+(1,))

x = Conv2D(filters=16, kernel_size=(7,7), activation='relu', name='EarlyConv')(input_image)
x = Conv2D(filters=32, kernel_size=(5,5), activation='relu')(x)
x = Conv2D(filters=64, kernel_size=(5,5), activation='relu')(x)
x = Conv2D(filters=128, kernel_size=(3,3), activation='relu', name='LastConv')(x)

x = GlobalAveragePooling2D()(x)
x = BatchNormalization()(x)
x = Dense(512, activation='relu')(x)
x = Dropout(rate=0.25)(x)

preds = Dense(2,activation='softmax')(x) #final layer with softmax activation

model = Model(inputs=input_image,outputs=preds)
model.summary()

In [0]:
radam = RAdamOptimizer(learning_rate=1e-3)
model.compile(optimizer=radam, loss='categorical_crossentropy', metrics = ['accuracy'])

In [0]:
#@title Create the callbacks for visualization
#@markdown To provide some illustration, several callbacks are instantiated. Not all are used below, though.

#@markdown Double-click the header row to expand this cell and inspect the definitions. 

x_val_g = val_generator.next()
x_val_img = np.array(x_val_g[0])
x_val_lbl = np.array(x_val_g[1])
val_class_zero = (np.array([
    el for el, label in zip(x_val_img, x_val_lbl)
    if np.all(label == np.array([1] + [0]))
][0:9]), None)
val_class_one = (np.array([
    el for el, label in zip(x_val_img, x_val_lbl)
    if np.all(label == np.array([0] + [1]))
][0:9]), None)

#@markdown Which layer to visualize in __GradCam__:
LAYER = 'MiddleConv' #@param  ['MiddleConv', 'EarlyConv', 'LastConv']

#@markdown __Occlusion Sensitivity__ patch size:
PATCH_SIZE = 16 #@param {'type':'integer'}
cam_cb_00 = tfx.callbacks.GradCAMCallback(val_class_zero, layer_name='MiddleConv', class_index=0, output_dir='logs/GradCam/LastConv/classPDexplPD')
cam_cb_01 = tfx.callbacks.GradCAMCallback(val_class_zero, layer_name='MiddleConv', class_index=1, output_dir='logs/GradCam/LastConv/classPDexplHC')
cam_cb_10 = tfx.callbacks.GradCAMCallback(val_class_one, layer_name='MiddleConv', class_index=0, output_dir='logs/GradCam/MiddleConv/classHCexplPD')
cam_cb_11 = tfx.callbacks.GradCAMCallback(val_class_one, layer_name='MiddleConv', class_index=1, output_dir='logs/GradCam/MiddleConv/classHCexplHC')
occ_cb_00 =  tfx.callbacks.OcclusionSensitivityCallback(val_class_zero,class_index=0, patch_size=PATCH_SIZE, output_dir='logs/Occlusion/classPDexplPD')
occ_cb_01 =  tfx.callbacks.OcclusionSensitivityCallback(val_class_zero,class_index=1, patch_size=PATCH_SIZE, output_dir='logs/Occlusion/classPDexplHC')
occ_cb_10 =  tfx.callbacks.OcclusionSensitivityCallback(val_class_one,class_index=0, patch_size=PATCH_SIZE, output_dir='logs/Occlusion/classHCexplPD')
occ_cb_11 =  tfx.callbacks.OcclusionSensitivityCallback(val_class_one,class_index=1, patch_size=PATCH_SIZE, output_dir='logs/Occlusion/classHCexplHC')
tf_cb = tf.keras.callbacks.TensorBoard(histogram_freq=5)

In [30]:
# train the model on the new data for a few epochs. Use the callbacks only afterwards to speed up the process.
history = model.fit_generator(generator=train_generator,
                              steps_per_epoch=train_generator.n//train_generator.batch_size,
                              epochs=50,
                             validation_data=val_generator,
                             validation_steps=val_generator.n//val_generator.batch_size,
                             verbose=0,
                             callbacks=[tf_cb])

In [34]:
# After that, only train two epochs to generate the visualizations. This is costly!
# Look into the embedded TensorBoard above to see results.
history = model.fit_generator(generator=train_generator,
                              steps_per_epoch=train_generator.n//train_generator.batch_size,
                              epochs=30,
                             validation_data=val_generator,
                             validation_steps=val_generator.n//val_generator.batch_size,
                             verbose=2,
                             callbacks=[cam_cb_00, cam_cb_01,cam_cb_10, cam_cb_11, occ_cb_00, occ_cb_01, occ_cb_10, occ_cb_11])

Epoch 1/30
34/34 - 3s - loss: 0.0857 - accuracy: 0.9700 - val_loss: 0.7028 - val_accuracy: 0.8698
Epoch 2/30


/usr/local/lib/python3.6/dist-packages/tf_explain/utils/display.py:65: RuntimeWarning: invalid value encountered in true_divide
  map = (map - np.min(map)) / (map.max() - map.min())


34/34 - 3s - loss: 0.0500 - accuracy: 0.9793 - val_loss: 0.1406 - val_accuracy: 0.9635
Epoch 3/30
34/34 - 3s - loss: 0.0400 - accuracy: 0.9840 - val_loss: 0.0376 - val_accuracy: 0.9896
Epoch 4/30
34/34 - 3s - loss: 0.0471 - accuracy: 0.9897 - val_loss: 0.0809 - val_accuracy: 0.9635
Epoch 5/30
34/34 - 3s - loss: 0.0478 - accuracy: 0.9850 - val_loss: 0.1787 - val_accuracy: 0.9479
Epoch 6/30
34/34 - 3s - loss: 0.0418 - accuracy: 0.9840 - val_loss: 0.0373 - val_accuracy: 0.9896
Epoch 7/30
34/34 - 3s - loss: 0.0402 - accuracy: 0.9850 - val_loss: 0.0568 - val_accuracy: 0.9844
Epoch 8/30
34/34 - 3s - loss: 0.0578 - accuracy: 0.9835 - val_loss: 0.8552 - val_accuracy: 0.8802
Epoch 9/30
34/34 - 3s - loss: 0.0435 - accuracy: 0.9840 - val_loss: 0.2497 - val_accuracy: 0.9323
Epoch 10/30
34/34 - 3s - loss: 0.0206 - accuracy: 0.9942 - val_loss: 0.1224 - val_accuracy: 0.9688
Epoch 11/30
34/34 - 3s - loss: 0.0386 - accuracy: 0.9878 - val_loss: 0.0500 - val_accuracy: 0.9792
Epoch 12/30
34/34 - 3s - loss

In [0]:
%load_ext tensorboard

In [33]:
import datetime, os

logs_base_dir = "./logs"
os.makedirs(logs_base_dir, exist_ok=True)
%tensorboard --logdir {logs_base_dir}

Reusing TensorBoard on port 6006 (pid 1108), started 1:27:59 ago. (Use '!kill 1108' to kill it.)

# A toy example from the `tf_explain` authors.

The original code by the tf_explain authors, taken from https://github.com/sicara/tf-explain/blob/master/examples/callbacks/mnist.py

The original code does not cast the input data to float. This may cause a crash depending on TF version.

In [1]:
try:
  import talos
except:
  !pip install talos
  import talos

Using TensorFlow backend.


In [0]:
p = {
    'patch_size': [4, 8, 12]
}

In [4]:
import numpy as np
import tensorflow as tf
import tf_explain

INPUT_SHAPE = (28, 28, 1)
NUM_CLASSES = 10

AVAILABLE_DATASETS = {
    'mnist': tf.keras.datasets.mnist,
    'fashion_mnist': tf.keras.datasets.fashion_mnist,
}
DATASET_NAME = 'mnist'  # Choose between "mnist" and "fashion_mnist"

# Load dataset
dataset = AVAILABLE_DATASETS[DATASET_NAME]
(train_images, train_labels), (test_images, test_labels) = dataset.load_data()
train_images = train_images.astype(np.float32)
test_images = test_images.astype(np.float32)

# Convert from (28, 28) images to (28, 28, 1)
train_images = train_images[..., tf.newaxis]
test_images = test_images[..., tf.newaxis]

# One hot encore labels 0, 1, .., 9 to [0, 0, .., 1, 0, 0]
train_labels = tf.keras.utils.to_categorical(train_labels, num_classes=NUM_CLASSES)
test_labels = tf.keras.utils.to_categorical(test_labels, num_classes=NUM_CLASSES)

def demo_model(x_train, y_train, x_val, y_val, params):
  # Create model
  img_input = tf.keras.Input(INPUT_SHAPE)

  x = tf.keras.layers.Conv2D(filters=32, kernel_size=(3, 3), activation='relu')(img_input)
  x = tf.keras.layers.Conv2D(filters=64, kernel_size=(3, 3), activation='relu', name='target_layer')(x)
  x = tf.keras.layers.MaxPool2D(pool_size=(2, 2))(x)

  x = tf.keras.layers.Dropout(0.25)(x)
  x = tf.keras.layers.Flatten()(x)

  x = tf.keras.layers.Dense(128, activation='relu')(x)
  x = tf.keras.layers.Dropout(0.5)(x)

  x = tf.keras.layers.Dense(NUM_CLASSES, activation='softmax')(x)

  model = tf.keras.Model(img_input, x)
  model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

  # Select a subset of the validation data to examine
  # Here, we choose 5 elements with label "0" == [1, 0, 0, .., 0]
  validation_class_zero = (np.array([
      el for el, label in zip(test_images, test_labels)
      if np.all(label == np.array([1] + [0] * 9))
  ][0:5]), None)
  # Select a subset of the validation data to examine
  # Here, we choose 5 elements with label "4" == [0, 0, 0, 0, 1, 0, 0, 0, 0, 0]
  validation_class_fours = (np.array([
      el for el, label in zip(test_images, test_labels)
      if np.all(label == np.array([0] * 4 + [1] + [0] * 5))
  ][0:5]), None)

  # Select a subset of the validation data to examine
  # Here, we choose 5 elements with label "3" == [0, 0, 0, 1, .., 0]
  validation_class_three = (np.array([
      el for el, label in zip(test_images, test_labels)
      if np.all(label == np.array([0] * 3 + [1] + [0] * 6))
  ][0:5]), None)
  # Select a subset of the validation data to examine
  # Here, we choose 5 elements with label "9" == [0, 0, 0, 0, 0, 0, 0, 0, 0, 1]
  validation_class_nine = (np.array([
      el for el, label in zip(test_images, test_labels)
      if np.all(label == np.array([0] * 9 + [1]))
  ][0:5]), None)

  # Instantiate callbacks
  # class_index value should match the validation_data selected above
  callbacks = [
      tf_explain.callbacks.GradCAMCallback(validation_class_three, 'target_layer', class_index=3, output_dir='logs/GradCam/class3expl3'),
      tf_explain.callbacks.GradCAMCallback(validation_class_three, 'target_layer', class_index=9, output_dir='logs/GradCam/class3expl9'),
      tf_explain.callbacks.GradCAMCallback(validation_class_nine, 'target_layer', class_index=3, output_dir='logs/GradCam/class9expl3'),
      tf_explain.callbacks.GradCAMCallback(validation_class_nine, 'target_layer', class_index=9, output_dir='logs/GradCam/class9expl9'),
  #    tf_explain.callbacks.ActivationsVisualizationCallback(validation_class_zero, layers_name=['target_layer']),
  #    tf_explain.callbacks.SmoothGradCallback(validation_class_zero, class_index=0, num_samples=15, noise=1.),
  #    tf_explain.callbacks.OcclusionSensitivityCallback(validation_class_zero, class_index=0, patch_size=4),
  ]
  callbacks = [
      tf_explain.callbacks.OcclusionSensitivityCallback(validation_class_three, class_index=3, patch_size=params['patch_size']),
      tf_explain.callbacks.OcclusionSensitivityCallback(validation_class_three, class_index=9, patch_size=params['patch_size']),
      tf_explain.callbacks.OcclusionSensitivityCallback(validation_class_nine, class_index=3, patch_size=params['patch_size']),
      tf_explain.callbacks.OcclusionSensitivityCallback(validation_class_nine, class_index=9, patch_size=params['patch_size']),
  ]
  # Start training
  out = model.fit(train_images.astype(np.float32), train_labels, epochs=15, callbacks=callbacks)
  return out, model


ModuleNotFoundError: ignored